In [1]:
import numpy as np
import torch
import torch.nn as nn
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import wandb
from torch.optim.lr_scheduler import StepLR
from torch.utils.data import Dataset, DataLoader
from torch.utils.data import DataLoader, TensorDataset
from sklearn.metrics import r2_score
from matplotlib.colors import ListedColormap, Normalize
from matplotlib.cm import ScalarMappable
from matplotlib.lines import Line2D
from datetime import datetime
from sklearn.preprocessing import StandardScaler
import os
from helper_toy import train_VAE 

In [2]:
X_train = pd.read_csv('../datasets/Toy/X_train.csv',index_col=0)  
X_test = pd.read_csv('../datasets/Toy/X_test.csv',index_col=0)  
y_train = pd.read_csv('../datasets/Toy/y_train.csv',index_col=0)  
y_test = pd.read_csv('../datasets/Toy/y_test.csv',index_col=0)  
X_train_with_confounder=X_train.drop(columns=['x1'])
X_test_with_confounder=X_test.drop(columns=['x1'])
print(X_train.shape)
print(X_train_with_confounder)
print(X_test.shape)
print(X_test_with_confounder.shape)
print(X_train.columns)
print(X_train_with_confounder.columns)
X_train_with_confounder



(160000, 6)
              x0        x2        x3          x4  x5
32964   0.574323 -0.615475  1.180319  151.990726   0
40454  -0.082656 -0.937215  1.358132  157.451914   0
147570 -0.656177 -0.379655  0.503405  155.168497   0
115765  0.657298  1.034703  1.491080  165.186907   0
106561  0.049916  0.864532  1.574197  167.052309   1
...          ...       ...       ...         ...  ..
192225  0.721711 -1.048236  1.675111  156.763660   0
128687  1.317903  0.855172  1.414137  166.230565   0
1325    1.000358  1.189846  2.469026  176.208885   1
73364   1.429729 -0.373535  0.709987  165.980706   1
26686  -0.138872 -0.255932  0.847396  156.582525   0

[160000 rows x 5 columns]
(40000, 6)
(40000, 5)
Index(['x0', 'x1', 'x2', 'x3', 'x4', 'x5'], dtype='object')
Index(['x0', 'x2', 'x3', 'x4', 'x5'], dtype='object')


x0        x2        x3          x4  x5
32964   0.574323 -0.615475  1.180319  151.990726   0
40454  -0.082656 -0.937215  1.358132  157.451914   0
147570 -0.656177 -0.379655  0.503405  155.168497   0
115765  0.657298  1.034703  1.491080  165.186907   0
106561  0.049916  0.864532  1.574197  167.052309   1
...          ...       ...       ...         ...  ..
192225  0.721711 -1.048236  1.675111  156.763660   0
128687  1.317903  0.855172  1.414137  166.230565   0
1325    1.000358  1.189846  2.469026  176.208885   1
73364   1.429729 -0.373535  0.709987  165.980706   1
26686  -0.138872 -0.255932  0.847396  156.582525   0

[160000 rows x 5 columns]

In [20]:
# Sampling the X dataframes
X_train_sample = X_train_with_confounder.sample(frac=0.2, )
X_test_sample = X_test_with_confounder.sample(frac=0.2, )


# Using the indices from the X samples to select the corresponding rows in the y dataframes
y_train_sample = y_train.loc[X_train_sample.index]
y_test_sample = y_test.loc[X_test_sample.index]

In [21]:

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_sample)
X_test_scaled = scaler.transform(X_test_sample)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [22]:
import itertools

# Define the ranges for your parameters
x_dim_values = [X_train_with_confounder.shape[1]]
z_dim_values = [3,4]
zz_dim_values = [1]
encoder_z_layers_values = [[10,10,10],[64,64,64]]
encoder_zz_layers_values = [[10,10]]
#decoder_layers_values = [[14,X_train_with_confounder.shape[1]],[32, 32,X_train_with_confounder.shape[1]],[128,128,128,X_train_with_confounder.shape[1]]]
fc_z_to_y_layers_values = [[12,12,1],[32,32,32,1]]

# Get all combinations
configurations = list(itertools.product(x_dim_values, z_dim_values, zz_dim_values, encoder_z_layers_values, encoder_zz_layers_values, fc_z_to_y_layers_values))

# Convert to a list of dictionaries
config_dicts = [{'x_dim': x_dim, 'z_dim': z_dim, 'zz_dim': zz_dim, 'encoder_z_layers': encoder_z_layers, 'encoder_zz_layers': encoder_zz_layers, 'decoder_layers': encoder_z_layers+ [x_dim], 'fc_z_to_y_layers': fc_z_to_y_layers} for x_dim, z_dim, zz_dim, encoder_z_layers, encoder_zz_layers, fc_z_to_y_layers in configurations]
print(config_dicts)

[{'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [12, 12, 1]}, {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 1

In [23]:
# Define betas
BETAS=[
    #{'b1': 6, 'b2': 1, 'b3': 1, 'b4': 6,'b5':1},
    #{'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1000,'b5':1},
    #{'b1': 100, 'b2': 1, 'b3': 100, 'b4': 100,'b5':1},
    #{'b1': 100,'b2': 1, 'b3': 1, 'b4': 10,'b5':1},  
    {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1,'b5':1},
    {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000,'b5':1}
]
import itertools

# Define the ranges for your parameters
lr_values = [1e-3]
batch_size_values = [512,1024]
#num_epochs_values = [100,500]
num_epochs_values = [300,500]
# Get all combinations
configs = list(itertools.product(config_dicts, BETAS, lr_values, batch_size_values, num_epochs_values))

# Convert to a list of dictionaries
configs = [{'config': config, 'beta': beta, 'lr': lr, 'batch_size': bs, 'num_epochs': epochs} for config, beta, lr, bs, epochs in configs]
print(len(configs))

64


# No Freez and z and zz to y 

In [41]:
from sklearn.model_selection import KFold
from tqdm import tqdm
kf = KFold(n_splits=3, shuffle=True)
results = pd.DataFrame()

In [42]:
df_list = []
for conf in configs:
    r2s=[]
    r2s_test=[]
    losses_train=[]
    losses_test=[]
    for train_index, test_index in kf.split(X_train_scaled):
        X_train_cv, X_val_cv = X_train_scaled[train_index], X_train_scaled[test_index]
        y_train_cv, y_val_cv = y_train.to_numpy()[train_index], y_train.to_numpy()[test_index]
        model,r2,loss_train,loss_test=train_VAE(X_train_cv,X_val_cv,X_val_cv,y_train_cv,y_val_cv,conf,'./Test',save_pictures=False,freeze_weights=False)
        r2s.append(r2)
        losses_train.append(loss_train)
        losses_test.append(loss_test)
        test_ds = TensorDataset(torch.Tensor(X_test_scaled), torch.Tensor(y_test.values))
        y_true = np.array([y.numpy() for _, y in test_ds],dtype=object)
        _,_,_,_,_,outputs = model(torch.Tensor(X_test_scaled).to(device))
        y_pred = outputs.cpu().detach().numpy()
        r2_test = r2_score(y_true, y_pred)
        r2s_test.append(r2_test)
        print("R^2 Test score:", r2_test)
    # Adding each config, mean R2 score, mean loss_train, and mean loss_test to the dictionary
    df_list.append({'config': conf, 
                    'mean_r2': np.mean(r2s),
                    'mean_r2_test': np.mean(r2s_test),
                    'mean_loss_train': np.mean(losses_train),
                    'mean_loss_test': np.mean(losses_test)})

# Creating DataFrame from list of dictionaries
df = pd.DataFrame(df_list)


{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 1024, 'num_epochs': 100}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]              33
            Linear-8                    [-1, 3]              33
            Linear-9                   [-1, 10]              40

Epoch 1, loss: 1657.6842041015625
Epoch 2, loss: 1640.712890625
Epoch 3, loss: 1621.8255615234375
Epoch 4, loss: 1569.182861328125
Epoch 5, loss: 1480.639404296875
Epoch 6, loss: 1360.2862548828125
Epoch 7, loss: 1156.7947998046875
Epoch 8, loss: 1004.8171997070312
Epoch 9, loss: 741.2822265625
Epoch 10, loss: 534.2411499023438
Epoch 11, loss: 460.56982421875
Epoch 12, loss: 333.73956298828125
Epoch 13, loss: 283.5705871582031
Epoch 14, loss: 229.60543823242188
Epoch 15, loss: 210.4181365966797
Epoch 16, loss: 188.0567169189453
Epoch 17, loss: 192.94065856933594
Epoch 18, loss: 173.81332397460938
Epoch 19, loss: 138.96005249023438
Epoch 20, loss: 140.2080535888672
Epoch 21, loss: 122.59466552734375
Epoch 22, loss: 102.59693145751953
Epoch 23, loss: 88.22501373291016
Epoch 24, loss: 80.7586669921875
Epoch 25, loss: 69.45668029785156
Epoch 26, loss: 71.28343963623047
Epoch 27, loss: 60.490013122558594
Epoch 28, loss: 57.81623458862305
Epoch 29, loss: 60.583072662353516
Epoch 30, loss: 63

Epoch 65, loss: 49.64197540283203
Epoch 66, loss: 51.718196868896484
Epoch 67, loss: 55.07423782348633
Epoch 68, loss: 58.349090576171875
Epoch 69, loss: 46.64301681518555
Epoch 70, loss: 42.08819580078125
Epoch 71, loss: 50.53802490234375
Epoch 72, loss: 58.91302490234375
Epoch 73, loss: 47.8076171875
Epoch 74, loss: 50.314334869384766
Epoch 75, loss: 55.62993621826172
Epoch 76, loss: 47.78038787841797
Epoch 77, loss: 57.44058609008789
Epoch 78, loss: 51.51383972167969
Epoch 79, loss: 49.724578857421875
Epoch 80, loss: 48.16363525390625
Epoch 81, loss: 51.196285247802734
Epoch 82, loss: 57.959571838378906
Epoch 83, loss: 53.231834411621094
Epoch 84, loss: 52.80512619018555
Epoch 85, loss: 44.65829849243164
Epoch 86, loss: 45.425655364990234
Epoch 87, loss: 45.071468353271484
Epoch 88, loss: 42.82375717163086
Epoch 89, loss: 47.43293380737305
Epoch 90, loss: 46.66465759277344
Epoch 91, loss: 56.250240325927734
Epoch 92, loss: 54.22118377685547
Epoch 93, loss: 47.45526885986328
Epoch 94

Epoch 129, loss: 50.620201110839844
Epoch 130, loss: 45.22687530517578
Epoch 131, loss: 48.0184211730957
Epoch 132, loss: 53.418914794921875
Epoch 133, loss: 49.60185241699219
Epoch 134, loss: 48.80743408203125
Epoch 135, loss: 54.43967819213867
Epoch 136, loss: 48.83361053466797
Epoch 137, loss: 49.02286148071289
Epoch 138, loss: 45.731101989746094
Epoch 139, loss: 47.015682220458984
Epoch 140, loss: 60.28525161743164
Epoch 141, loss: 53.70485305786133
Epoch 142, loss: 55.10737991333008
Epoch 143, loss: 48.97670364379883
Epoch 144, loss: 53.36082458496094
Epoch 145, loss: 41.93601989746094
Epoch 146, loss: 44.848228454589844
Epoch 147, loss: 51.33799362182617
Epoch 148, loss: 46.88783645629883
Epoch 149, loss: 48.71929931640625
Epoch 150, loss: 45.24814224243164
Epoch 151, loss: 50.559051513671875
Epoch 152, loss: 47.27619171142578
Epoch 153, loss: 53.24980926513672
Epoch 154, loss: 49.803443908691406
Epoch 155, loss: 48.91838836669922
Epoch 156, loss: 51.13340759277344
Epoch 157, los

Epoch 363, loss: 53.09176254272461
Epoch 364, loss: 53.44911193847656
Epoch 365, loss: 54.114662170410156
Epoch 366, loss: 50.673255920410156
Epoch 367, loss: 50.688758850097656
Epoch 368, loss: 48.308868408203125
Epoch 369, loss: 58.261043548583984
Epoch 370, loss: 47.62111282348633
Epoch 371, loss: 49.99114227294922
Epoch 372, loss: 48.656532287597656
Epoch 373, loss: 52.545501708984375
Epoch 374, loss: 51.233943939208984
Epoch 375, loss: 47.07008743286133
Epoch 376, loss: 49.84444046020508
Epoch 377, loss: 49.05278778076172
Epoch 378, loss: 54.77677536010742
Epoch 379, loss: 42.940185546875
Epoch 380, loss: 53.909183502197266
Epoch 381, loss: 52.41477584838867
Epoch 382, loss: 59.501914978027344
Epoch 383, loss: 61.0777587890625
Epoch 384, loss: 52.237457275390625
Epoch 385, loss: 45.832218170166016
Epoch 386, loss: 49.920257568359375
Epoch 387, loss: 51.53145217895508
Epoch 388, loss: 50.72462463378906
Epoch 389, loss: 49.59183120727539
Epoch 390, loss: 51.51301193237305
Epoch 391,

...

Epoch 23, loss: 673.6755981445312
Epoch 24, loss: 662.7117919921875
Epoch 25, loss: 563.3077392578125
Epoch 26, loss: 485.2348937988281
Epoch 27, loss: 463.20501708984375
Epoch 28, loss: 406.2117919921875
Epoch 29, loss: 369.0528564453125
Epoch 30, loss: 314.4884948730469
Epoch 31, loss: 311.517578125
Epoch 32, loss: 287.1005859375
Epoch 33, loss: 264.1515197753906
Epoch 34, loss: 282.3684387207031
Epoch 35, loss: 260.64788818359375
Epoch 36, loss: 252.60296630859375
Epoch 37, loss: 242.50717163085938
Epoch 38, loss: 219.9827423095703
Epoch 39, loss: 230.16629028320312
Epoch 40, loss: 238.81314086914062
Epoch 41, loss: 193.0681610107422
Epoch 42, loss: 203.64141845703125
Epoch 43, loss: 209.49710083007812
Epoch 44, loss: 182.845458984375
Epoch 45, loss: 177.5597381591797
Epoch 46, loss: 153.63040161132812
Epoch 47, loss: 146.29197692871094
Epoch 48, loss: 157.77882385253906
Epoch 49, loss: 149.82855224609375
Epoch 50, loss: 141.1571502685547
Epoch 51, loss: 121.0935287475586
Epoch 52, 

Epoch 259, loss: 47.93149948120117
Epoch 260, loss: 46.90212631225586
Epoch 261, loss: 58.18943405151367
Epoch 262, loss: 48.5643424987793
Epoch 263, loss: 54.761322021484375
Epoch 264, loss: 47.70458221435547
Epoch 265, loss: 70.56626892089844
Epoch 266, loss: 50.30815124511719
Epoch 267, loss: 50.99042892456055
Epoch 268, loss: 54.666221618652344
Epoch 269, loss: 55.07234191894531
Epoch 270, loss: 50.97344207763672
Epoch 271, loss: 55.78614044189453
Epoch 272, loss: 51.955928802490234
Epoch 273, loss: 47.20475769042969
Epoch 274, loss: 59.82720184326172
Epoch 275, loss: 56.27907943725586
Epoch 276, loss: 45.5879020690918
Epoch 277, loss: 48.595703125
Epoch 278, loss: 52.62227249145508
Epoch 279, loss: 51.715084075927734
Epoch 280, loss: 52.09230041503906
Epoch 281, loss: 47.34444046020508
Epoch 282, loss: 52.20923614501953
Epoch 283, loss: 55.032222747802734
Epoch 284, loss: 56.681217193603516
Epoch 285, loss: 55.51480484008789
Epoch 286, loss: 55.82774353027344
Epoch 287, loss: 50.1

Epoch 493, loss: 48.00159454345703
Epoch 494, loss: 50.567508697509766
Epoch 495, loss: 44.56210708618164
Epoch 496, loss: 53.783935546875
Epoch 497, loss: 53.49104690551758
Epoch 498, loss: 58.79413604736328
Epoch 499, loss: 53.5667610168457
Epoch 500, loss: 47.188743591308594
R^2 score: -0.00033429666805484537
R^2 Test score: -0.0005388546144318163
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 2048, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4          

Epoch 156, loss: 49.875144958496094
Epoch 157, loss: 58.55989456176758
Epoch 158, loss: 51.24303436279297
Epoch 159, loss: 51.963844299316406
Epoch 160, loss: 47.82536697387695
Epoch 161, loss: 53.56944274902344
Epoch 162, loss: 51.72036361694336
Epoch 163, loss: 61.788177490234375
Epoch 164, loss: 49.181427001953125
Epoch 165, loss: 50.19062042236328
Epoch 166, loss: 52.918453216552734
Epoch 167, loss: 55.582759857177734
Epoch 168, loss: 44.65232849121094
Epoch 169, loss: 54.200103759765625
Epoch 170, loss: 50.790672302246094
Epoch 171, loss: 51.81105041503906
Epoch 172, loss: 54.83554458618164
Epoch 173, loss: 62.81350326538086
Epoch 174, loss: 43.65145492553711
Epoch 175, loss: 54.59764862060547
Epoch 176, loss: 58.16355514526367
Epoch 177, loss: 44.27713394165039
Epoch 178, loss: 47.0844841003418
Epoch 179, loss: 45.90026092529297
Epoch 180, loss: 50.8765869140625
Epoch 181, loss: 53.10356140136719
Epoch 182, loss: 46.50751495361328
Epoch 183, loss: 52.584075927734375
Epoch 184, lo

KeyboardInterrupt: 

In [45]:
df = pd.DataFrame(df_list)

In [49]:
df.iloc[29]

config             {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...
mean_r2                                                      0.98886
mean_r2_test                                                0.989017
mean_loss_train                                             5.327162
mean_loss_test                                               5.38513
Name: 29, dtype: object

In [50]:
df.iloc[29].config

{'config': {'x_dim': 5,
  'z_dim': 3,
  'zz_dim': 1,
  'encoder_z_layers': [64, 64, 64],
  'encoder_zz_layers': [10, 10],
  'decoder_layers': [64, 64, 64, 5],
  'fc_z_to_y_layers': [32, 32, 32, 1]},
 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1},
 'lr': 0.001,
 'batch_size': 1024,
 'num_epochs': 500}

# Freeze and z and zz to y

In [24]:
from sklearn.model_selection import KFold
from tqdm import tqdm
kf = KFold(n_splits=5, shuffle=True)
results = pd.DataFrame()
df_list = []
for conf in configs:
    r2s=[]
    r2s_test=[]
    losses_train=[]
    losses_test=[]
    for train_index, test_index in kf.split(X_train_scaled):
        X_train_cv, X_val_cv = X_train_scaled[train_index], X_train_scaled[test_index]
        y_train_cv, y_val_cv = y_train_sample.to_numpy()[train_index], y_train_sample.to_numpy()[test_index]
        model,r2,loss_train,loss_test=train_VAE(X_train_cv,X_val_cv,X_val_cv,y_train_cv,y_val_cv,conf,'./Test',save_pictures=False,freeze_weights=True,partial=100,offset=50)
        r2s.append(r2)
        losses_train.append(loss_train)
        losses_test.append(loss_test)
        test_ds = TensorDataset(torch.Tensor(X_test_scaled), torch.Tensor(y_test_sample.values))
        y_true = np.array([y.numpy() for _, y in test_ds],dtype=object)
        _,_,_,_,_,outputs = model(torch.Tensor(X_test_scaled).to(device))
        y_pred = outputs.cpu().detach().numpy()
        r2_test = r2_score(y_true, y_pred)
        r2s_test.append(r2_test)
        print("R^2 Test score:", r2_test)
    # Adding each config, mean R2 score, mean loss_train, and mean loss_test to the dictionary
    df_list.append({'config': conf, 
                    'mean_r2': np.mean(r2s),
                    'mean_r2_test': np.mean(r2s_test),
                    'mean_loss_train': np.mean(losses_train),
                    'mean_loss_test': np.mean(losses_test)})

# Creating DataFrame from list of dictionaries
df3 = pd.DataFrame(df_list)


{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 300}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]              33
            Linear-8                    [-1, 3]              33
            Linear-9                   [-1, 10]              40


Epoch 101, loss: 1653.209716796875
Epoch 151, loss: 51.52171325683594
Epoch 201, loss: 47.78403854370117
Epoch 251, loss: 50.27054977416992
R^2 score: -0.05000282170412218
R^2 Test score: -0.052334408276625055
{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 300}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10

Epoch 1, loss: 22.857582092285156
Epoch 51, loss: 1.0169475078582764
Epoch 101, loss: 1648.2672119140625
Epoch 151, loss: 53.4323844909668
Epoch 201, loss: 51.65117263793945
Epoch 251, loss: 60.1778564453125
Epoch 301, loss: 56.799339294433594
Epoch 351, loss: 48.24649429321289
Epoch 401, loss: 54.80691146850586
Epoch 451, loss: 47.264244079589844
R^2 score: -0.061380818410517124
R^2 Test score: -0.05655453788858389
{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3        

Epoch 1, loss: 8.875829696655273
Epoch 51, loss: 1.000650405883789
Epoch 101, loss: 1650.311767578125
Epoch 151, loss: 51.22105407714844
Epoch 201, loss: 49.577823638916016
Epoch 251, loss: 54.132843017578125
Epoch 301, loss: 55.593528747558594
Epoch 351, loss: 56.43963623046875
Epoch 401, loss: 49.56749725341797
Epoch 451, loss: 51.832149505615234
R^2 score: -0.06726004397256347
R^2 Test score: -0.04384957018133884
{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3        

Epoch 1, loss: 25.44137954711914
Epoch 51, loss: 1.0078661441802979
Epoch 101, loss: 1652.4439697265625
Epoch 151, loss: 64.78807830810547
Epoch 201, loss: 61.07330322265625
Epoch 251, loss: 59.272953033447266
R^2 score: -0.415348712183198
R^2 Test score: -0.41584365573721316
{'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 5], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 1, 'b2': 1, 'b3': 1, 'b4': 1, 'b5': 1}, 'lr': 0.001, 'batch_size': 1024, 'num_epochs': 300}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              60
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1

...

Epoch 1, loss: 7933.85888671875
Epoch 51, loss: 3238.75390625
Epoch 101, loss: 16499838.0
Epoch 151, loss: 166237.8125
Epoch 201, loss: 165749.1875
Epoch 251, loss: 186808.34375
Epoch 301, loss: 188768.40625
Epoch 351, loss: 174495.890625
Epoch 401, loss: 187697.421875
Epoch 451, loss: 175679.84375
R^2 score: 0.8853361159672164
R^2 Test score: 0.8899768523674376
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
       

Epoch 1, loss: 8216.580078125
Epoch 51, loss: 3147.984130859375
Epoch 101, loss: 16519164.0
Epoch 151, loss: 228670.78125
Epoch 201, loss: 225816.265625
Epoch 251, loss: 198146.765625
Epoch 301, loss: 216707.828125
Epoch 351, loss: 216855.40625
Epoch 401, loss: 209092.109375
Epoch 451, loss: 207928.75
R^2 score: 0.8252999503487156
R^2 Test score: 0.8271231230896459
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 512, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
    

Epoch 1, loss: 9513.5537109375
Epoch 51, loss: 5199.56787109375
Epoch 101, loss: 16527034.0
Epoch 151, loss: 267975.09375
Epoch 201, loss: 259017.234375
Epoch 251, loss: 266308.53125
R^2 score: 0.7135985277640773
R^2 Test score: 0.7326670849068215
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 1024, 'num_epochs': 300}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4

Epoch 1, loss: 9958.677734375
Epoch 51, loss: 5031.2919921875
Epoch 101, loss: 16548002.0
Epoch 151, loss: 238424.5625
Epoch 201, loss: 247820.625
Epoch 251, loss: 254855.296875
R^2 score: 0.7509257400984298
R^2 Test score: 0.7593708152599096
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 1024, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160


Epoch 1, loss: 9916.7197265625
Epoch 51, loss: 5125.04248046875
Epoch 101, loss: 16568408.0
Epoch 151, loss: 234106.03125
Epoch 201, loss: 248241.328125
Epoch 251, loss: 228113.953125
Epoch 301, loss: 230985.546875
Epoch 351, loss: 229533.125
Epoch 401, loss: 233486.859375
Epoch 451, loss: 244390.640625
R^2 score: 0.7713743439469085
R^2 Test score: 0.7871956190738877
{'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 5], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 1024, 'num_epochs': 500}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             384
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
 

In [13]:
from sklearn.model_selection import KFold
from tqdm import tqdm
kf = KFold(n_splits=5, shuffle=True)
results = pd.DataFrame()
df_list = []
for conf in configs:
    r2s=[]
    r2s_test=[]
    losses_train=[]
    losses_test=[]
    for train_index, test_index in kf.split(X_train_scaled):
        X_train_cv, X_val_cv = X_train_scaled[train_index], X_train_scaled[test_index]
        y_train_cv, y_val_cv = y_train.to_numpy()[train_index], y_train.to_numpy()[test_index]
        model,r2,loss_train,loss_test=train_VAE(X_train_cv,X_val_cv,X_val_cv,y_train_cv,y_val_cv,conf,'./Test',save_pictures=False,freeze_weights=True,partial=400,offset=200,z_and_zz_to_y=False)
        r2s.append(r2)
        losses_train.append(loss_train)
        losses_test.append(loss_test)
        test_ds = TensorDataset(torch.Tensor(X_test_scaled), torch.Tensor(y_test.values))
        y_true = np.array([y.numpy() for _, y in test_ds],dtype=object)
        _,_,_,_,_,outputs = model(torch.Tensor(X_test_scaled).to(device))
        y_pred = outputs.cpu().detach().numpy()
        r2_test = r2_score(y_true, y_pred)
        r2s_test.append(r2_test)
        print("R^2 Test score:", r2_test)
    # Adding each config, mean R2 score, mean loss_train, and mean loss_test to the dictionary
    df_list.append({'config': conf, 
                    'mean_r2': np.mean(r2s),
                    'mean_r2_test': np.mean(r2s_test),
                    'mean_loss_train': np.mean(losses_train),
                    'mean_loss_test': np.mean(losses_test)})

# Creating DataFrame from list of dictionaries
df4 = pd.DataFrame(df_list)


{'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 6], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 16, 'num_epochs': 600}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              70
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]              33
            Linear-8                    [-1, 3]              33
            Linear-9                   [-1, 10]          

Epoch 201, loss: 1271.9127197265625
Epoch 401, loss: 3634.568115234375
R^2 score: 0.8210215237168432
R^2 Test score: 0.6402763304679556
{'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 6], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 16, 'num_epochs': 600}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              70
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]  

Epoch 601, loss: 513.314697265625
R^2 score: 0.8022987529129448
R^2 Test score: 0.6128188422606196
{'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 6], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 16, 'num_epochs': 800}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              70
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]              33
            Linear-8  

Epoch 601, loss: 769.4639282226562
R^2 score: 0.7245727157914816
R^2 Test score: 0.6305884443160603
{'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 6], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 16, 'num_epochs': 1000}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              70
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]               0
            Linear-7                    [-1, 3]              33
            Linear-8

Epoch 201, loss: 1994.6376953125
Epoch 401, loss: 8203.1865234375
Epoch 601, loss: 744.71435546875
Epoch 801, loss: 516.451904296875
R^2 score: 0.7591270296292448
R^2 Test score: 0.6603927290751679
{'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': 1, 'encoder_z_layers': [10, 10, 10], 'encoder_zz_layers': [10, 10], 'decoder_layers': [10, 10, 10, 6], 'fc_z_to_y_layers': [12, 12, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 16, 'num_epochs': 1000}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 10]              70
              ReLU-2                   [-1, 10]               0
            Linear-3                   [-1, 10]             110
              ReLU-4                   [-1, 10]               0
            Linear-5                   [-1, 10]             110
              ReLU-6                   [-1, 10]   

...

Epoch 201, loss: 555.6329956054688
Epoch 401, loss: 7706.73681640625
R^2 score: 0.7688242813858087
R^2 Test score: 0.6130234330483216
{'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 6], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 32, 'num_epochs': 600}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             448
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160
              ReLU-6                   [-1, 64]               0
            Linear-7                    [-1, 4]

Epoch 201, loss: 621.5386962890625
Epoch 401, loss: 6444.44921875
R^2 score: 0.75451577616046
R^2 Test score: 0.6375948027906748
{'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 6], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 32, 'num_epochs': 800}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             448
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160
              ReLU-6                   [-1, 64]               0
            Linear-7                    [-1, 4]     

Epoch 201, loss: 635.635986328125
Epoch 401, loss: 6453.17626953125
Epoch 601, loss: 443.9038391113281
R^2 score: 0.7582465850249736
R^2 Test score: 0.6625731147758855
{'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 6], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 32, 'num_epochs': 800}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             448
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160
              ReLU-6                   [-1, 64]               0
            L

Epoch 201, loss: 586.313232421875
Epoch 401, loss: 4347.20556640625
Epoch 601, loss: 528.9098510742188
Epoch 801, loss: 544.1492309570312
R^2 score: 0.6590605041610875
R^2 Test score: 0.6520580144457457
{'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 6], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 32, 'num_epochs': 1000}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             448
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160
              ReLU-6                   [-

Epoch 201, loss: 626.0001220703125
Epoch 401, loss: 6220.54443359375
Epoch 601, loss: 586.0083618164062
Epoch 801, loss: 547.5289306640625
R^2 score: 0.7450131635886921
R^2 Test score: 0.6268118206300268
{'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': 1, 'encoder_z_layers': [64, 64, 64], 'encoder_zz_layers': [10, 10], 'decoder_layers': [64, 64, 64, 6], 'fc_z_to_y_layers': [32, 32, 32, 1]}, 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1}, 'lr': 0.001, 'batch_size': 32, 'num_epochs': 1000}
False
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                   [-1, 64]             448
              ReLU-2                   [-1, 64]               0
            Linear-3                   [-1, 64]           4,160
              ReLU-4                   [-1, 64]               0
            Linear-5                   [-1, 64]           4,160
              ReLU-6                   [

In [25]:
df3.sort_values(by=[mean_r2]).head(5)

config   mean_r2  mean_r2_test  \
0   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.071757     -0.067297   
1   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.040679     -0.035002   
2   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -1.325169     -1.290292   
3   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.248740     -0.234647   
4   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.656615      0.660123   
..                                                ...       ...           ...   
59  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.028111     -0.033470   
60  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.860531      0.865326   
61  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.861921      0.864595   
62  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.748446      0.756339   
63  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.777996      0.786118   

    mean_loss_train  mean_loss_test  
0         52.478210       52.511078  
1         51.690956       51.656883  
2         72.943970       72.652214  
3         56.193031       56.468239  
4         28.207239       28.202509  
..              ...             ...  
59        51.480194       51.413689  
60        18.872866       18.916357  
61        18.886875       18.710649  
62        25.410412       25.360476  
63        23.599783       23.758949  

[64 rows x 5 columns]

In [28]:
df3.sort_values(by=['mean_r2'],).head(-5)

config   mean_r2  mean_r2_test  \
2   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -1.325169     -1.290292   
18  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.522930     -0.512492   
34  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.414843     -0.422616   
19  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.256081     -0.240993   
3   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.248740     -0.234647   
54  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.230089     -0.193592   
50  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.108285     -0.103996   
35  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.100096     -0.107053   
33  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.091847     -0.087842   
0   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.071757     -0.067297   
32  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.067886     -0.072262   
16  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.066191     -0.064597   
51  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.065853     -0.060448   
38  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.056193     -0.032863   
26  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.055727     -0.047522   
49  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.055358     -0.057394   
48  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.046977     -0.045516   
1   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.040679     -0.035002   
42  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.039170     -0.035475   
17  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.037060     -0.036858   
27  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.032296     -0.031602   
10  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.028749     -0.025886   
59  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.028111     -0.033470   
43  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.026208     -0.026727   
58  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.025122     -0.025837   
11  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.022734     -0.021845   
24  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.016990     -0.014575   
6   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.016813      0.002545   
41  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.016446     -0.019563   
25  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.014522     -0.021573   
8   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.014145     -0.016479   
9   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ... -0.010894     -0.013327   
56  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.008829     -0.009444   
57  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.008668     -0.009700   
40  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ... -0.008624     -0.008973   
22  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.228577      0.241635   
7   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.304048      0.315069   
55  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.428313      0.441291   
39  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.460042      0.466466   
15  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.480347      0.484863   
47  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.509634      0.509292   
14  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.580792      0.579648   
46  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.586527      0.584367   
23  {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.601052      0.608258   
36  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.605395      0.612117   
37  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.621749      0.628640   
4   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.656615      0.660123   
5   {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...  0.669698      0.669175   
45  {'config': {'x_dim': 5, 'z_dim': 4, 'zz_dim': ...  0.741838      0.745619 

In [30]:
df3.iloc[13]

config             {'config': {'x_dim': 5, 'z_dim': 3, 'zz_dim': ...
mean_r2                                                     0.827691
mean_r2_test                                                0.830321
mean_loss_train                                            20.711399
mean_loss_test                                             20.942715
Name: 13, dtype: object

In [31]:
df3.iloc[13].config

{'config': {'x_dim': 5,
  'z_dim': 3,
  'zz_dim': 1,
  'encoder_z_layers': [10, 10, 10],
  'encoder_zz_layers': [10, 10],
  'decoder_layers': [10, 10, 10, 5],
  'fc_z_to_y_layers': [32, 32, 32, 1]},
 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1},
 'lr': 0.001,
 'batch_size': 512,
 'num_epochs': 500}

In [29]:
df3[13]

KeyError: 13

In [15]:
df4

config   mean_r2  mean_r2_test  \
0   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.760942      0.638280   
1   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.768109      0.630276   
2   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.762600      0.637904   
3   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.750013      0.648528   
4   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.744163      0.644739   
5   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.760770      0.648856   
6   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.714175      0.621920   
7   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.757878      0.632721   
8   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.728272      0.642879   
9   {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.720424      0.636158   
10  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.746479      0.626922   
11  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.749353      0.622002   
12  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.748853      0.625307   
13  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.766021      0.640527   
14  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.752153      0.646468   
15  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.759990      0.641817   
16  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.740657      0.620295   
17  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.718082      0.614755   
18  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.691941      0.585839   
19  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.747420      0.639596   
20  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.746665      0.625593   
21  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.755684      0.640498   
22  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.756390      0.645087   
23  {'config': {'x_dim': 6, 'z_dim': 3, 'zz_dim': ...  0.763227      0.646746   
24  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.752172      0.635927   
25  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.751501      0.612395   
26  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.748969      0.613601   
27  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.746623      0.644114   
28  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.738724      0.637049   
29  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.738905      0.609278   
30  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.738153      0.636254   
31  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.731916      0.625751   
32  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.742923      0.642049   
33  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.755469      0.624973   
34  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.763715      0.642004   
35  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.749102      0.643122   
36  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.736086      0.612797   
37  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.746935      0.644657   
38  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.745442      0.624672   
39  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.726575      0.621881   
40  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.767667      0.644936   
41  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.756536      0.625208   
42  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.749454      0.637192   
43  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.738977      0.619190   
44  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.744614      0.595116   
45  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.735071      0.612369   
46  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.753755      0.639900   
47  {'config': {'x_dim': 6, 'z_dim': 4, 'zz_dim': ...  0.712497      0.629611   

    mean_loss_train  mean_loss_test  
0          0.065567        0.068741  
1

In [13]:
configs[23]

{'config': {'x_dim': 6,
  'z_dim': 3,
  'zz_dim': 1,
  'encoder_z_layers': [64, 64, 64],
  'encoder_zz_layers': [10, 10],
  'decoder_layers': [64, 64, 64, 6],
  'fc_z_to_y_layers': [32, 32, 32, 1]},
 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1},
 'lr': 0.001,
 'batch_size': 32,
 'num_epochs': 1000}

In [14]:
configs[2]

{'config': {'x_dim': 6,
  'z_dim': 3,
  'zz_dim': 1,
  'encoder_z_layers': [10, 10, 10],
  'encoder_zz_layers': [10, 10],
  'decoder_layers': [10, 10, 10, 6],
  'fc_z_to_y_layers': [12, 12, 1]},
 'beta': {'b1': 10000, 'b2': 1, 'b3': 1, 'b4': 10000, 'b5': 1},
 'lr': 0.001,
 'batch_size': 16,
 'num_epochs': 1000}